<a href="https://colab.research.google.com/github/douglasmmachado/MedicineConsumption/blob/main/notebooks/division_approach/5_Forecasting.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# 5 - Forecasting and prediction



---



---



In [9]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from scipy import stats
import seaborn as sns
import math as m

from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestRegressor

from sklearn.tree import export_graphviz
from subprocess import call
from IPython.display import Image

from sklearn.metrics import r2_score, mean_absolute_error, mean_squared_error,  mean_absolute_percentage_error
from sklearn.model_selection import RandomizedSearchCV
from sklearn.preprocessing import StandardScaler

from sklearn.utils import shuffle
from sklearn.model_selection import GridSearchCV



df_h1_url ="https://raw.githubusercontent.com/douglasmmachado/ExploratoryDataAnalysis/main/datasets/division_approach/clustered/df_h1_clustered.csv"
df_h2_url ="https://raw.githubusercontent.com/douglasmmachado/ExploratoryDataAnalysis/main/datasets/division_approach/clustered/df_h2_clustered.csv"
df_h3_url ="https://raw.githubusercontent.com/douglasmmachado/ExploratoryDataAnalysis/main/datasets/division_approach/clustered/df_h3_clustered.csv"
df_h4_url ="https://raw.githubusercontent.com/douglasmmachado/ExploratoryDataAnalysis/main/datasets/division_approach/clustered/df_h4_clustered.csv"

df_h1 = pd.read_csv(df_h1_url)
df_h2 = pd.read_csv(df_h2_url)
df_h3 = pd.read_csv(df_h3_url)
df_h4 = pd.read_csv(df_h4_url)

# Convert numerical columns to string
for i, curr_df in enumerate([df_h1, df_h2, df_h3, df_h4]):
    numerical_columns = ['HOSPI_CODE_UCD']
    curr_df[numerical_columns] = curr_df[numerical_columns].astype('string')

medicines = ['3400892088310','3400892075761','3400892203645',
             '3400892065366','3400892052120','3400891996128',
             '3400893826706','3400893736135','3400893875490',
             '3400890837149','3400891235203','3400891225037',
             '3400891191226','3400892729589','3400892745848',
             '3400892697789','3400892761527','3400893022634',
             '3400892761695','3400892669236','3400892508566']

In [ ]:
df_h1.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1208 entries, 0 to 1207
Data columns (total 47 columns):
 #   Column             Non-Null Count  Dtype  
---  ------             --------------  -----  
 0   HOSPI_CODE_UCD     1208 non-null   int64  
 1   LIT_HC             1208 non-null   float64
 2   LIT_HP             1208 non-null   float64
 3   N_UFS              1208 non-null   float64
 4   PN_MEDICAL         1208 non-null   float64
 5   POPULATION         1208 non-null   float64
 6   P_MEDICAL          1208 non-null   float64
 7   QUANTITY           1208 non-null   float64
 8   QUANTITY_MA        1208 non-null   float64
 9   SEJ_MCO            1208 non-null   float64
 10  SEJ_SLD            1208 non-null   float64
 11  SEJ_SSR            1208 non-null   float64
 12  YEAR               1208 non-null   float64
 13  MONTH_1.0          1208 non-null   int64  
 14  MONTH_2.0          1208 non-null   int64  
 15  MONTH_3.0          1208 non-null   int64  
 16  MONTH_4.0          1208 

In [ ]:
df_h2.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 697 entries, 0 to 696
Data columns (total 47 columns):
 #   Column             Non-Null Count  Dtype  
---  ------             --------------  -----  
 0   HOSPI_CODE_UCD     697 non-null    int64  
 1   LIT_HC             697 non-null    float64
 2   LIT_HP             697 non-null    float64
 3   N_UFS              697 non-null    float64
 4   PN_MEDICAL         697 non-null    float64
 5   POPULATION         697 non-null    float64
 6   P_MEDICAL          697 non-null    float64
 7   QUANTITY           697 non-null    float64
 8   QUANTITY_MA        697 non-null    float64
 9   SEJ_MCO            697 non-null    float64
 10  SEJ_PSY            697 non-null    float64
 11  SEJ_SSR            697 non-null    float64
 12  YEAR               697 non-null    float64
 13  MONTH_1.0          697 non-null    int64  
 14  MONTH_2.0          697 non-null    int64  
 15  MONTH_3.0          697 non-null    int64  
 16  MONTH_4.0          697 non

In [ ]:
df_h3.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1397 entries, 0 to 1396
Data columns (total 49 columns):
 #   Column             Non-Null Count  Dtype  
---  ------             --------------  -----  
 0   HOSPI_CODE_UCD     1397 non-null   int64  
 1   LIT_HC             1397 non-null   float64
 2   LIT_HP             1397 non-null   float64
 3   N_UFS              1397 non-null   float64
 4   PN_MEDICAL         1397 non-null   float64
 5   POPULATION         1397 non-null   float64
 6   P_MEDICAL          1397 non-null   float64
 7   QUANTITY           1397 non-null   float64
 8   QUANTITY_MA        1397 non-null   float64
 9   SEJ_HAD            1397 non-null   float64
 10  SEJ_MCO            1397 non-null   float64
 11  SEJ_PSY            1397 non-null   float64
 12  SEJ_SLD            1397 non-null   float64
 13  SEJ_SSR            1397 non-null   float64
 14  YEAR               1397 non-null   float64
 15  MONTH_1.0          1397 non-null   int64  
 16  MONTH_2.0          1397 

In [ ]:
df_h4.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 770 entries, 0 to 769
Data columns (total 48 columns):
 #   Column             Non-Null Count  Dtype  
---  ------             --------------  -----  
 0   HOSPI_CODE_UCD     770 non-null    int64  
 1   LIT_HC             770 non-null    float64
 2   LIT_HP             770 non-null    float64
 3   N_UFS              770 non-null    float64
 4   PN_MEDICAL         770 non-null    float64
 5   POPULATION         770 non-null    float64
 6   P_MEDICAL          770 non-null    float64
 7   QUANTITY           770 non-null    float64
 8   QUANTITY_MA        770 non-null    float64
 9   SEJ_MCO            770 non-null    float64
 10  SEJ_PSY            770 non-null    float64
 11  SEJ_SLD            770 non-null    float64
 12  SEJ_SSR            770 non-null    float64
 13  YEAR               770 non-null    float64
 14  MONTH_1.0          770 non-null    int64  
 15  MONTH_2.0          770 non-null    int64  
 16  MONTH_3.0          770 non

## 5.1 - New database composition based on clusters

In [3]:
features = ['HOSPI_CODE_UCD', 'LIT_HC', 'LIT_HP', 'N_ETB', 'N_UFS', 'PN_MEDICAL',
       'POPULATION', 'P_MEDICAL', 'QUANTITY', 'SEJ_HAD',
       'SEJ_MCO', 'SEJ_PSY', 'SEJ_SLD', 'SEJ_SSR', 'MONTH_1.0', 'MONTH_2.0',
       'MONTH_3.0', 'MONTH_4.0', 'MONTH_5.0', 'MONTH_6.0', 'MONTH_7.0',
       'MONTH_8.0', 'MONTH_9.0', 'MONTH_10.0', 'MONTH_11.0', 'MONTH_12.0', 'CLUSTER']

In [4]:
features_h1 = list(set(features) - {"N_ETB", "SEJ_HAD", "SEJ_PSY"})
features_h2 = list(set(features) - {'SEJ_HAD', 'SEJ_SLD', 'N_ETB'})
features_h3 = list(set(features) - {'N_ETB'})
features_h4 = list(set(features) - {'SEJ_HAD', 'N_ETB'})

## Baseline for each medicine and hospital

In [11]:
import plotly.graph_objects as go

def plot_pred(y_pred, y_test, medicine):
    # Create a scatter plot for y_pred
    fig = go.Figure(data=go.Scatter(x=np.arange(len(y_pred)), y=y_pred, mode='markers', name='y_pred', marker=dict(symbol='circle')))

    # Add scatter plot for y_test
    fig.add_trace(go.Scatter(x=np.arange(len(y_test)), y=y_test, mode='markers', name='y_test', marker=dict(symbol='x')))

    # Set axes labels and title
    fig.update_layout(xaxis_title='Test samples', yaxis_title='Quantity',
                      title=f'y_pred and y_test for medicine: {medicine}')

    # Show the plot
    fig.show()


In [7]:
import plotly.graph_objects as go

def plot_mape(y_pred, y_test, medicine, epsilon=0.001):
    mape_array = np.abs(y_test - y_pred) / np.maximum(epsilon, np.abs(y_test))

    # Create a scatter plot for MAPE
    fig = go.Figure(data=go.Scatter(x=np.arange(len(y_pred)), y=mape_array, mode='markers', name='MAPE'))

    # Set axes labels and title
    fig.update_layout(xaxis_title='Test samples', yaxis_title='MAPE',
                      title=f'MAPE for medicine: {medicine}')

    # Show the plot
    fig.show()

In [6]:
def test_1_baseline(df, medicine, df_scores):
  print()
  print(100*'-')
  print('Medicine:' + str(medicine))

  X = df[df['HOSPI_CODE_UCD'] == medicine].drop(['QUANTITY', 'HOSPI_CODE_UCD'], axis=1).values

  scaler = StandardScaler()
  X_scaled = scaler.fit_transform(X)

  y = df[df['HOSPI_CODE_UCD'] == medicine]['QUANTITY'].values

  X_scaled, y = shuffle(X_scaled, y, random_state=42)

  if m.ceil(len(X_scaled) * 0.1) == 1:
    print('Dataset too small')
    test_size = 2
  else:
    test_size = 0.1

  # Split the data into training and testing sets
  X_train, X_test, y_train, y_test = train_test_split(X_scaled, y,
                                                      test_size = test_size,
                                                      random_state = 42)
  print(f'Size of data set: {len(X)}')
  print(f'Size of training set: {len(X_train)}')
  print(f'Size of test set: {len(X_test)}')

  # Define the parameter distributions for RandomizedSearchCV
  param_grid = {
      'max_depth': np.arange(2, 8, 1),
      'n_estimators': np.arange(2, max(int(m.ceil(len(X_train)*0.1)),3), 1),
      'max_features': ['sqrt']
  }
  depth_len = param_grid['max_depth'].size
  estimators_len = param_grid['n_estimators'].size

  print(f'Size of grid search: {depth_len * estimators_len}')

  # Create the RandomizedSearchCV object
  grid_search = GridSearchCV(estimator=RandomForestRegressor(random_state=42),
                             param_grid=param_grid,
                             scoring = 'neg_mean_absolute_percentage_error',
                             cv = 5,
                             n_jobs = -1)

  ''' >3 : the fold and candidate parameter indexes
      are also displayed together with the starting time of the computation.
  '''
  # Fit the RandomizedSearchCV object to the data
  grid_search.fit(X_train, y_train)

  # Get the best estimator
  best_estimator = grid_search.best_estimator_

  # Make predictions using the best estimator
  y_pred = best_estimator.predict(X_test)

  # Calculate R^2 score
  r2 = r2_score(y_test, y_pred)

  # Calculate MAE
  mae = mean_absolute_error(y_test, y_pred)

  # Calculate MAPE
  mape = mean_absolute_percentage_error(y_test, y_pred)

  # Calculate RMSE
  rmse = np.sqrt(mean_squared_error(y_test, y_pred))

  # Print the best parameters, best score, and evaluation metrics
  print('Best Parameters: ', grid_search.best_params_)
  print('Training Score (MAPE): ', round(grid_search.best_score_, 3))
  print(10*'-' + 'Test scores' + 10*'-')
  print('R^2 Score:', round(r2, 3))
  print('MAE:', round(mae, 3))
  print('MAPE:', round(mape, 3))
  print('RMSE:', round(rmse, 3))
  print()


  # Create the new row as a DataFrame
  new_row = pd.DataFrame({'HOSPI_CODE_UCD': ['CODE_UCD_'+str(medicine)],
                          'R2': [r2],
                          'RMSE': [rmse],
                          'MAE': [mae],
                          'MAPE': [mape]})

  # Append the new row to the DataFrame
  df_scores = pd.concat([df_scores, new_row], ignore_index=True)

  # plot pred x test
  plot_pred(y_pred, y_test, medicine)
  print()


  plot_mape(y_pred, y_test, medicine)
  print()

  # Return the updated DataFrame
  return df_scores


In [12]:
df_prediction_scores_h1 = pd.DataFrame(columns=['HOSPI_CODE_UCD', 'R2', 'RMSE', 'MAE', 'MAPE'])

for medicine in medicines:

  df_prediction_scores_h1 = test_1_baseline(df_h1[features_h1], medicine, df_prediction_scores_h1)

df_prediction_scores_h1


----------------------------------------------------------------------------------------------------
Medicine:3400892088310
Size of data set: 47
Size of training set: 42
Size of test set: 5
Size of grid search: 18
Best Parameters:  {'max_depth': 2, 'max_features': 'sqrt', 'n_estimators': 4}
Training Score (MAPE):  -15.513
----------Test scores----------
R^2 Score: 0.595
MAE: 511.584
MAPE: 4.996
RMSE: 653.248





----------------------------------------------------------------------------------------------------
Medicine:3400892075761
Size of data set: 63
Size of training set: 56
Size of test set: 7
Size of grid search: 24
Best Parameters:  {'max_depth': 7, 'max_features': 'sqrt', 'n_estimators': 4}
Training Score (MAPE):  -0.442
----------Test scores----------
R^2 Score: 0.796
MAE: 128.911
MAPE: 0.207
RMSE: 162.542





----------------------------------------------------------------------------------------------------
Medicine:3400892203645
Size of data set: 60
Size of training set: 54
Size of test set: 6
Size of grid search: 24
Best Parameters:  {'max_depth': 5, 'max_features': 'sqrt', 'n_estimators': 5}
Training Score (MAPE):  -1.404
----------Test scores----------
R^2 Score: 0.85
MAE: 190.775
MAPE: 0.442
RMSE: 212.687





----------------------------------------------------------------------------------------------------
Medicine:3400892065366
Size of data set: 60
Size of training set: 54
Size of test set: 6
Size of grid search: 24
Best Parameters:  {'max_depth': 6, 'max_features': 'sqrt', 'n_estimators': 2}
Training Score (MAPE):  -0.431
----------Test scores----------
R^2 Score: 0.238
MAE: 698.062
MAPE: 0.218
RMSE: 1139.577





----------------------------------------------------------------------------------------------------
Medicine:3400892052120
Size of data set: 54
Size of training set: 48
Size of test set: 6
Size of grid search: 18
Best Parameters:  {'max_depth': 3, 'max_features': 'sqrt', 'n_estimators': 3}
Training Score (MAPE):  -0.518
----------Test scores----------
R^2 Score: -0.311
MAE: 410.855
MAPE: 0.156
RMSE: 536.882



...



----------------------------------------------------------------------------------------------------
Medicine:3400893022634
Size of data set: 68
Size of training set: 61
Size of test set: 7
Size of grid search: 30
Best Parameters:  {'max_depth': 6, 'max_features': 'sqrt', 'n_estimators': 2}
Training Score (MAPE):  -8.291
----------Test scores----------
R^2 Score: 0.886
MAE: 346.482
MAPE: 0.293
RMSE: 442.881





----------------------------------------------------------------------------------------------------
Medicine:3400892761695
Size of data set: 60
Size of training set: 54
Size of test set: 6
Size of grid search: 24
Best Parameters:  {'max_depth': 2, 'max_features': 'sqrt', 'n_estimators': 3}
Training Score (MAPE):  -0.191
----------Test scores----------
R^2 Score: -1.482
MAE: 242.029
MAPE: 0.14
RMSE: 284.283





----------------------------------------------------------------------------------------------------
Medicine:3400892669236
Size of data set: 33
Size of training set: 29
Size of test set: 4
Size of grid search: 6
Best Parameters:  {'max_depth': 3, 'max_features': 'sqrt', 'n_estimators': 2}
Training Score (MAPE):  -62.017
----------Test scores----------
R^2 Score: 0.944
MAE: 809.48
MAPE: 0.236
RMSE: 889.767





----------------------------------------------------------------------------------------------------
Medicine:3400892508566
Size of data set: 60
Size of training set: 54
Size of test set: 6
Size of grid search: 24
Best Parameters:  {'max_depth': 5, 'max_features': 'sqrt', 'n_estimators': 3}
Training Score (MAPE):  -3.157
----------Test scores----------
R^2 Score: 0.757
MAE: 640.668
MAPE: 0.562
RMSE: 677.099



HOSPI_CODE_UCD        R2         RMSE          MAE       MAPE
0   CODE_UCD_3400892088310  0.594736   653.248406   511.584276   4.995967
1   CODE_UCD_3400892075761  0.796174   162.541843   128.910714   0.206923
2   CODE_UCD_3400892203645  0.849805   212.686801   190.775159   0.441506
3   CODE_UCD_3400892065366  0.238292  1139.577047   698.062500   0.217979
4   CODE_UCD_3400892052120 -0.311412   536.882289   410.854894   0.155960
5   CODE_UCD_3400891996128  0.905172  5870.620147  4379.166323   0.126162
6   CODE_UCD_3400893826706  0.741695   769.993375   605.947659   6.798433
7   CODE_UCD_3400893736135  0.892141   295.137233   208.449074   0.904096
8   CODE_UCD_3400893875490  0.938086   929.827864   766.093585   1.053473
9   CODE_UCD_3400890837149  0.495100   756.472927   634.404762   2.418064
10  CODE_UCD_3400891235203 -0.044570   426.964708   363.586420   0.389157
11  CODE_UCD_3400891225037  0.670423  4048.078781  2882.953762  21.041290
12  CODE_UCD_3400891191226  0.334292   360.958446   278.241204   0.100614
13  CODE_UCD_3400892729589  0.691230   665.839333   599.506166   0.197184
14  CODE_UCD_3400892745848  0.168636  1052.247997   922.697917   0.126893
15  CODE_UCD_3400892697789  0.162698   363.750252   287.583617   5.076720
16  CODE_UCD_3400892761527  0.618640  1214.338347   896.751674   5.307836
17  CODE_UCD_3400893022634  0.885923   442.881016   346.482331   0.293359
18  CODE_UCD_3400892761695 -1.481864   284.282841   242.029474   0.139671
19  CODE_UCD_3400892669236  0.944397   889.766699   809.480479   0.235627
20  CODE_UCD_3400892508566  0.756573   677.099200   640.668117   0.562159

In [13]:
df_prediction_scores_h2 = pd.DataFrame(columns=['HOSPI_CODE_UCD', 'R2', 'RMSE', 'MAE', 'MAPE'])

for medicine in medicines:

  df_prediction_scores_h2 = test_1_baseline(df_h2[features_h2], medicine, df_prediction_scores_h2)

df_prediction_scores_h2


----------------------------------------------------------------------------------------------------
Medicine:3400892088310
Size of data set: 34
Size of training set: 30
Size of test set: 4
Size of grid search: 6
Best Parameters:  {'max_depth': 2, 'max_features': 'sqrt', 'n_estimators': 2}
Training Score (MAPE):  -0.108
----------Test scores----------
R^2 Score: 0.117
MAE: 178.07
MAPE: 0.061
RMSE: 220.321





----------------------------------------------------------------------------------------------------
Medicine:3400892075761
Size of data set: 34
Size of training set: 30
Size of test set: 4
Size of grid search: 6
Best Parameters:  {'max_depth': 4, 'max_features': 'sqrt', 'n_estimators': 2}
Training Score (MAPE):  -0.117
----------Test scores----------
R^2 Score: 0.087
MAE: 212.365
MAPE: 0.094
RMSE: 246.222





----------------------------------------------------------------------------------------------------
Medicine:3400892203645
Size of data set: 33
Size of training set: 29
Size of test set: 4
Size of grid search: 6
Best Parameters:  {'max_depth': 2, 'max_features': 'sqrt', 'n_estimators': 2}
Training Score (MAPE):  -0.158
----------Test scores----------
R^2 Score: -2.995
MAE: 380.002
MAPE: 0.118
RMSE: 388.768





----------------------------------------------------------------------------------------------------
Medicine:3400892065366
Size of data set: 34
Size of training set: 30
Size of test set: 4
Size of grid search: 6
Best Parameters:  {'max_depth': 3, 'max_features': 'sqrt', 'n_estimators': 2}
Training Score (MAPE):  -0.128
----------Test scores----------
R^2 Score: 0.543
MAE: 1205.502
MAPE: 0.175
RMSE: 1432.802





----------------------------------------------------------------------------------------------------
Medicine:3400892052120
Size of data set: 34
Size of training set: 30
Size of test set: 4
Size of grid search: 6
Best Parameters:  {'max_depth': 4, 'max_features': 'sqrt', 'n_estimators': 2}
Training Score (MAPE):  -0.152
----------Test scores----------
R^2 Score: 0.356
MAE: 173.571
MAPE: 0.106
RMSE: 202.447



...



----------------------------------------------------------------------------------------------------
Medicine:3400893022634
Size of data set: 34
Size of training set: 30
Size of test set: 4
Size of grid search: 6
Best Parameters:  {'max_depth': 3, 'max_features': 'sqrt', 'n_estimators': 2}
Training Score (MAPE):  -0.122
----------Test scores----------
R^2 Score: -6.216
MAE: 750.729
MAPE: 0.139
RMSE: 807.258





----------------------------------------------------------------------------------------------------
Medicine:3400892761695
Size of data set: 34
Size of training set: 30
Size of test set: 4
Size of grid search: 6
Best Parameters:  {'max_depth': 4, 'max_features': 'sqrt', 'n_estimators': 2}
Training Score (MAPE):  -0.064
----------Test scores----------
R^2 Score: -0.492
MAE: 1003.867
MAPE: 0.075
RMSE: 1335.705





----------------------------------------------------------------------------------------------------
Medicine:3400892669236
Size of data set: 34
Size of training set: 30
Size of test set: 4
Size of grid search: 6
Best Parameters:  {'max_depth': 2, 'max_features': 'sqrt', 'n_estimators': 2}
Training Score (MAPE):  -0.075
----------Test scores----------
R^2 Score: 0.664
MAE: 321.042
MAPE: 0.039
RMSE: 367.824





----------------------------------------------------------------------------------------------------
Medicine:3400892508566
Size of data set: 23
Size of training set: 20
Size of test set: 3
Size of grid search: 6
Best Parameters:  {'max_depth': 2, 'max_features': 'sqrt', 'n_estimators': 2}
Training Score (MAPE):  -0.438
----------Test scores----------
R^2 Score: -1.936
MAE: 12.87
MAPE: 0.271
RMSE: 13.991



HOSPI_CODE_UCD        R2         RMSE          MAE      MAPE
0   CODE_UCD_3400892088310  0.117229   220.321067   178.070098  0.060649
1   CODE_UCD_3400892075761  0.086693   246.221519   212.365196  0.094120
2   CODE_UCD_3400892203645 -2.995292   388.768104   380.002273  0.118213
3   CODE_UCD_3400892065366  0.543373  1432.801968  1205.502273  0.175105
4   CODE_UCD_3400892052120  0.356091   202.447122   173.571429  0.105890
5   CODE_UCD_3400891996128  0.028788  6645.223808  4908.037500  0.067699
6   CODE_UCD_3400893826706 -1.317099   215.810738   184.755208  0.095074
7   CODE_UCD_3400893736135 -0.403940   855.808983   828.937500  0.223669
8   CODE_UCD_3400893875490  0.077161   452.252879   424.187500  0.048187
9   CODE_UCD_3400890837149 -0.266060   376.929292   275.762054  0.100627
10  CODE_UCD_3400891235203 -1.540373   286.447154   207.312092  0.206478
11  CODE_UCD_3400891225037  0.585544  1447.788543  1297.400397  0.087184
12  CODE_UCD_3400891191226  0.623506   320.612257   171.250000  0.111636
13  CODE_UCD_3400892729589  0.067343   401.008215   275.692857  0.060400
14  CODE_UCD_3400892745848  0.165682   785.410031   651.792039  0.223001
15  CODE_UCD_3400892697789  0.043242   149.706540   127.329545  0.154569
16  CODE_UCD_3400892761527 -3.842295  1382.223970  1161.963439  0.108914
17  CODE_UCD_3400893022634 -6.216387   807.257727   750.729167  0.139026
18  CODE_UCD_3400892761695 -0.492106  1335.704523  1003.867063  0.075040
19  CODE_UCD_3400892669236  0.663817   367.824366   321.041621  0.039272
20  CODE_UCD_3400892508566 -1.936343    13.991289    12.870370  0.270525

In [14]:
df_prediction_scores_h3 = pd.DataFrame(columns=['HOSPI_CODE_UCD', 'R2', 'RMSE', 'MAE', 'MAPE'])

for medicine in medicines:

  df_prediction_scores_h3 = test_1_baseline(df_h3[features_h3], medicine, df_prediction_scores_h3)

df_prediction_scores_h3


----------------------------------------------------------------------------------------------------
Medicine:3400892088310
Size of data set: 68
Size of training set: 61
Size of test set: 7
Size of grid search: 30
Best Parameters:  {'max_depth': 6, 'max_features': 'sqrt', 'n_estimators': 3}
Training Score (MAPE):  -0.069
----------Test scores----------
R^2 Score: -2.088
MAE: 587.517
MAPE: 0.138
RMSE: 695.965





----------------------------------------------------------------------------------------------------
Medicine:3400892075761
Size of data set: 68
Size of training set: 61
Size of test set: 7
Size of grid search: 30
Best Parameters:  {'max_depth': 2, 'max_features': 'sqrt', 'n_estimators': 5}
Training Score (MAPE):  -0.11
----------Test scores----------
R^2 Score: 0.461
MAE: 245.129
MAPE: 0.092
RMSE: 271.725





----------------------------------------------------------------------------------------------------
Medicine:3400892203645
Size of data set: 68
Size of training set: 61
Size of test set: 7
Size of grid search: 30
Best Parameters:  {'max_depth': 3, 'max_features': 'sqrt', 'n_estimators': 2}
Training Score (MAPE):  -0.114
----------Test scores----------
R^2 Score: -0.767
MAE: 455.704
MAPE: 0.094
RMSE: 522.42





----------------------------------------------------------------------------------------------------
Medicine:3400892065366
Size of data set: 68
Size of training set: 61
Size of test set: 7
Size of grid search: 30
Best Parameters:  {'max_depth': 5, 'max_features': 'sqrt', 'n_estimators': 4}
Training Score (MAPE):  -0.068
----------Test scores----------
R^2 Score: -0.097
MAE: 549.203
MAPE: 0.079
RMSE: 659.246





----------------------------------------------------------------------------------------------------
Medicine:3400892052120
Size of data set: 68
Size of training set: 61
Size of test set: 7
Size of grid search: 30
Best Parameters:  {'max_depth': 4, 'max_features': 'sqrt', 'n_estimators': 2}
Training Score (MAPE):  -0.135
----------Test scores----------
R^2 Score: 0.773
MAE: 171.732
MAPE: 0.178
RMSE: 224.86



...



----------------------------------------------------------------------------------------------------
Medicine:3400893022634
Size of data set: 46
Size of training set: 41
Size of test set: 5
Size of grid search: 18
Best Parameters:  {'max_depth': 3, 'max_features': 'sqrt', 'n_estimators': 3}
Training Score (MAPE):  -0.073
----------Test scores----------
R^2 Score: -0.16
MAE: 282.245
MAPE: 0.084
RMSE: 375.929





----------------------------------------------------------------------------------------------------
Medicine:3400892761695
Size of data set: 68
Size of training set: 61
Size of test set: 7
Size of grid search: 30
Best Parameters:  {'max_depth': 2, 'max_features': 'sqrt', 'n_estimators': 4}
Training Score (MAPE):  -0.053
----------Test scores----------
R^2 Score: -0.349
MAE: 1101.301
MAPE: 0.043
RMSE: 1134.201





----------------------------------------------------------------------------------------------------
Medicine:3400892669236
Size of data set: 68
Size of training set: 61
Size of test set: 7
Size of grid search: 30
Best Parameters:  {'max_depth': 5, 'max_features': 'sqrt', 'n_estimators': 6}
Training Score (MAPE):  -0.064
----------Test scores----------
R^2 Score: 0.207
MAE: 369.653
MAPE: 0.033
RMSE: 572.771





----------------------------------------------------------------------------------------------------
Medicine:3400892508566
Size of data set: 68
Size of training set: 61
Size of test set: 7
Size of grid search: 30
Best Parameters:  {'max_depth': 2, 'max_features': 'sqrt', 'n_estimators': 3}
Training Score (MAPE):  -0.123
----------Test scores----------
R^2 Score: -0.063
MAE: 607.673
MAPE: 0.126
RMSE: 634.305



HOSPI_CODE_UCD         R2         RMSE          MAE      MAPE
0   CODE_UCD_3400892088310  -2.087801   695.964991   587.516931  0.138236
1   CODE_UCD_3400892075761   0.461337   271.724513   245.128925  0.091882
2   CODE_UCD_3400892203645  -0.766697   522.419656   455.704314  0.094275
3   CODE_UCD_3400892065366  -0.096935   659.246384   549.202664  0.079148
4   CODE_UCD_3400892052120   0.773463   224.860196   171.731695  0.178457
5   CODE_UCD_3400891996128   0.010579  5350.936390  4620.745762  0.046371
6   CODE_UCD_3400893826706   0.579055   874.014666   637.346817  0.108364
7   CODE_UCD_3400893736135 -13.668160   917.114640   798.582766  0.172098
8   CODE_UCD_3400893875490   0.739438   353.111702   314.488884  0.023721
9   CODE_UCD_3400890837149   0.320315   301.450744   237.144901  0.065040
10  CODE_UCD_3400891235203   0.260869  1394.443321  1035.960518  0.428211
11  CODE_UCD_3400891225037   0.928458   517.460856   442.293891  0.047424
12  CODE_UCD_3400891191226   0.268239   749.854831   581.367593  0.095256
13  CODE_UCD_3400892729589   0.638558   224.413602   188.696861  0.028541
14  CODE_UCD_3400892745848   0.432885   117.869299   109.857143  0.284004
15  CODE_UCD_3400892697789   0.024684   373.973678   321.476964  0.212190
16  CODE_UCD_3400892761527   0.133506  2067.970059  1874.499587  0.062824
17  CODE_UCD_3400893022634  -0.160007   375.928619   282.244715  0.084166
18  CODE_UCD_3400892761695  -0.348917  1134.200571  1101.300711  0.042701
19  CODE_UCD_3400892669236   0.206951   572.770684   369.653181  0.032819
20  CODE_UCD_3400892508566  -0.062723   634.304912   607.673239  0.126267

In [15]:
df_prediction_scores_h4 = pd.DataFrame(columns=['HOSPI_CODE_UCD', 'R2', 'RMSE', 'MAE', 'MAPE'])

for medicine in medicines:

  df_prediction_scores_h4 = test_1_baseline(df_h4[features_h4], medicine, df_prediction_scores_h4)

df_prediction_scores_h4


----------------------------------------------------------------------------------------------------
Medicine:3400892088310
Size of data set: 22
Size of training set: 19
Size of test set: 3
Size of grid search: 6
Best Parameters:  {'max_depth': 4, 'max_features': 'sqrt', 'n_estimators': 2}
Training Score (MAPE):  -0.291
----------Test scores----------
R^2 Score: -0.125
MAE: 2358.0
MAPE: 0.797
RMSE: 3000.582





----------------------------------------------------------------------------------------------------
Medicine:3400892075761
Size of data set: 39
Size of training set: 35
Size of test set: 4
Size of grid search: 12
Best Parameters:  {'max_depth': 5, 'max_features': 'sqrt', 'n_estimators': 3}
Training Score (MAPE):  -0.102
----------Test scores----------
R^2 Score: 0.158
MAE: 800.332
MAPE: 0.078
RMSE: 1011.842





----------------------------------------------------------------------------------------------------
Medicine:3400892203645
Size of data set: 39
Size of training set: 35
Size of test set: 4
Size of grid search: 12
Best Parameters:  {'max_depth': 4, 'max_features': 'sqrt', 'n_estimators': 3}
Training Score (MAPE):  -0.161
----------Test scores----------
R^2 Score: -0.015
MAE: 1078.214
MAPE: 0.102
RMSE: 1241.067





----------------------------------------------------------------------------------------------------
Medicine:3400892065366
Size of data set: 39
Size of training set: 35
Size of test set: 4
Size of grid search: 12
Best Parameters:  {'max_depth': 2, 'max_features': 'sqrt', 'n_estimators': 3}
Training Score (MAPE):  -0.097
----------Test scores----------
R^2 Score: -0.049
MAE: 3187.5
MAPE: 0.156
RMSE: 3685.813





----------------------------------------------------------------------------------------------------
Medicine:3400892052120
Size of data set: 39
Size of training set: 35
Size of test set: 4
Size of grid search: 12
Best Parameters:  {'max_depth': 6, 'max_features': 'sqrt', 'n_estimators': 3}
Training Score (MAPE):  -0.148
----------Test scores----------
R^2 Score: -0.47
MAE: 1030.401
MAPE: 0.121
RMSE: 1299.366



...



----------------------------------------------------------------------------------------------------
Medicine:3400893022634
Dataset too small
Size of data set: 8
Size of training set: 6
Size of test set: 2
Size of grid search: 6
Best Parameters:  {'max_depth': 2, 'max_features': 'sqrt', 'n_estimators': 2}
Training Score (MAPE):  -0.38
----------Test scores----------
R^2 Score: -270.548
MAE: 988.125
MAPE: 0.331
RMSE: 988.723





----------------------------------------------------------------------------------------------------
Medicine:3400892761695
Size of data set: 39
Size of training set: 35
Size of test set: 4
Size of grid search: 12
Best Parameters:  {'max_depth': 5, 'max_features': 'sqrt', 'n_estimators': 3}
Training Score (MAPE):  -0.086
----------Test scores----------
R^2 Score: -2.026
MAE: 2184.324
MAPE: 0.22
RMSE: 2371.163





----------------------------------------------------------------------------------------------------
Medicine:3400892669236
Size of data set: 38
Size of training set: 34
Size of test set: 4
Size of grid search: 12
Best Parameters:  {'max_depth': 2, 'max_features': 'sqrt', 'n_estimators': 3}
Training Score (MAPE):  -0.188
----------Test scores----------
R^2 Score: -0.457
MAE: 4153.376
MAPE: 0.155
RMSE: 4936.617





----------------------------------------------------------------------------------------------------
Medicine:3400892508566
Size of data set: 39
Size of training set: 35
Size of test set: 4
Size of grid search: 12
Best Parameters:  {'max_depth': 3, 'max_features': 'sqrt', 'n_estimators': 3}
Training Score (MAPE):  -0.164
----------Test scores----------
R^2 Score: -0.851
MAE: 1457.532
MAPE: 0.19
RMSE: 1720.274



HOSPI_CODE_UCD          R2          RMSE           MAE      MAPE
0   CODE_UCD_3400892088310   -0.125124   3000.581944   2358.000000  0.796576
1   CODE_UCD_3400892075761    0.158087   1011.842015    800.332341  0.077826
2   CODE_UCD_3400892203645   -0.014677   1241.067472   1078.214286  0.102070
3   CODE_UCD_3400892065366   -0.049212   3685.812597   3187.500000  0.155625
4   CODE_UCD_3400892052120   -0.469889   1299.365501   1030.400794  0.120961
5   CODE_UCD_3400891996128   -2.046136  22749.596520  18273.541667  0.093047
6   CODE_UCD_3400893826706    0.017427   1034.522323    805.000000  0.143660
7   CODE_UCD_3400893736135   -3.837125   1503.217597   1324.219426  0.179590
8   CODE_UCD_3400893875490    0.813051   1075.732162   1051.633126  0.046038
9   CODE_UCD_3400890837149   -0.067308   3387.658486   2745.454545  0.185565
10  CODE_UCD_3400891235203    0.017807   1881.865964   1685.590278  0.369471
11  CODE_UCD_3400891225037  -12.769553   4963.376543   4701.833333  0.211889
12  CODE_UCD_3400891191226   -0.259002    872.680091    743.879310  0.089005
13  CODE_UCD_3400892729589   -2.015848   4436.398495   3822.036325  0.311161
14  CODE_UCD_3400892745848    0.850309   1053.072977   1011.805556  0.081090
15  CODE_UCD_3400892697789   -5.602517   1401.796264   1389.950397  0.113850
16  CODE_UCD_3400892761527   -0.984966   2148.482345   1930.833333  0.317457
17  CODE_UCD_3400893022634 -270.547960    988.722740    988.125000  0.331488
18  CODE_UCD_3400892761695   -2.025893   2371.162673   2184.324074  0.219725
19  CODE_UCD_3400892669236   -0.456569   4936.616511   4153.375926  0.154688
20  CODE_UCD_3400892508566   -0.851036   1720.274288   1457.532051  0.190374

## 5.2 - Building forecasting models based on clusters

In [23]:
def train_test_split_modified(df, random_state = 42, test_size = 0.1, Shuffle = False):
  df_iter = df.copy()

  np.random.seed(random_state)

  X_train = []
  y_train = []

  X_test = []
  y_test = []

  columns = df.columns

  df_train = pd.DataFrame(columns=columns)
  df_test = pd.DataFrame(columns=columns)
  i = 0
  for medicine in df_iter.HOSPI_CODE_UCD.unique():
    df_temp = df_iter[df_iter['HOSPI_CODE_UCD'] == medicine]
    i += len(df_temp)
    n_samples = len(df_temp)
    test_samples = max(m.ceil(n_samples * test_size), 2)

    if n_samples == 1:
      print('There is only one sample')
      test_samples = 1


    for _ in range(test_samples):
      random_index = np.random.choice(df_temp.index)
      random_row = df_temp.loc[random_index].to_frame().T

      # Concatenate the new row to the original DataFrame
      df_test = pd.concat([df_test, random_row], ignore_index=False)

      # Remove the selected index from df_temp
      df_temp = df_temp.drop(random_index)

    df_iter = df_iter.drop(df_iter[df_iter['HOSPI_CODE_UCD'] == medicine].index)

  # Get the indices of rows to exclude from df
  exclude_indices = df_test.index

  # Create df_train by dropping the rows specified by the exclude_indices from df
  df_train = df.drop(exclude_indices)

  if shuffle:
    X_train, y_train = shuffle(df_train.drop(['QUANTITY', 'CLUSTER'], axis=1), df_train.QUANTITY.values, random_state = random_state)
    X_test, y_test = shuffle(df_test.drop(['QUANTITY', 'CLUSTER'], axis=1).values, df_test.QUANTITY.values, random_state = random_state)

  return X_train, X_test, y_train, y_test

In [24]:
def test_2_clustering(df, df_scores, medicines):
  for cluster in df.CLUSTER.unique():
    print()
    print(100*'-')
    print(f'Cluster: {cluster}')

    # Perform the train-test split with shuffled samples
    X_train, X_test, y_train, y_test = train_test_split_modified(df[df['CLUSTER'] == cluster])
    print(f'Size of data set: {len(X_train) + len(X_test)}')
    print(f'Size of training set: {len(X_train)}')
    print(f'Size of test set: {len(X_test)}')

    df_test = pd.DataFrame(X_test, columns = df.drop(['QUANTITY', 'CLUSTER'], axis=1).copy().columns)
    df_test['QUANTITY'] = y_test

    # Define the parameter distributions for RandomizedSearchCV
    param_grid = {
        'max_depth': np.arange(2, 8, 1),
        'n_estimators': np.arange(2, max(int(m.ceil(len(X_train)*0.1)),3), 1),
        'max_features': ['sqrt']
    }

    depth_len = param_grid['max_depth'].size
    estimators_len = param_grid['n_estimators'].size

    print(f'Size of grid search: {depth_len * estimators_len}')

    # Create the RandomizedSearchCV object
    grid_search = GridSearchCV(estimator=RandomForestRegressor(random_state=42),
                              param_grid=param_grid,
                              scoring = 'neg_mean_absolute_percentage_error',
                              cv = 5,
                              n_jobs = -1)

    ''' >3 : the fold and candidate parameter indexes
        are also displayed together with the starting time of the computation.
    '''

    scaler = StandardScaler()
    X_train_scaled = scaler.fit_transform(X_train)

    # Fit the RandomizedSearchCV object to the data
    grid_search.fit(X_train_scaled, y_train)
    print("Finished training")

    # Get the best estimator
    best_estimator = grid_search.best_estimator_

    for medicine in df_test.HOSPI_CODE_UCD.unique():
      print()
      print(100*'-')
      print('Medicine:' + str(medicine))

      X_test_medicine = df_test[df_test['HOSPI_CODE_UCD'] == medicine].drop(['QUANTITY'], axis=1).copy().values

      scaler = StandardScaler()
      X_test_scaled = scaler.fit_transform(X_test_medicine)

      y_test_medicine = df_test[df_test['HOSPI_CODE_UCD'] == medicine]['QUANTITY'].copy().values

      # Make predictions using the best estimator
      y_pred = best_estimator.predict(X_test_scaled)

      # Calculate R^2 score
      r2 = r2_score(y_test_medicine, y_pred)

      # Calculate MAE
      mae = mean_absolute_error(y_test_medicine, y_pred)

      # Calculate MAPE
      mape = mean_absolute_percentage_error(y_test_medicine, y_pred)

      # Calculate RMSE
      rmse = np.sqrt(mean_squared_error(y_test_medicine, y_pred))

      # Print the best parameters, best score, and evaluation metrics

      # Print the best parameters, best score, and evaluation metrics
      print('Best Parameters: ', grid_search.best_params_)
      print('Training Score (MAPE): ', round(grid_search.best_score_, 3))
      print(10*'-' + 'Test scores' + 10*'-')
      print('R^2 Score:', round(r2, 3))
      print('MAE:', round(mae, 3))
      print('MAPE:', round(mape, 3))
      print('RMSE:', round(rmse, 3))
      print()


      # Create the new row as a DataFrame
      new_row = pd.DataFrame({'CLUSTER': [cluster],
                              'HOSPI_CODE_UCD': ['CODE_UCD_'+str(int(medicine))],
                              'R2': [r2],
                              'RMSE': [rmse],
                              'MAE': [mae],
                              'MAPE': [mape]})

      # Append the new row to the DataFrame
      df_scores = pd.concat([df_scores, new_row], ignore_index=True)

      plot_pred(y_pred, y_test_medicine, medicine)
      print()

      plot_mape(y_pred, y_test_medicine, medicine)
      print()

  # Return the updated DataFrame
  return df_scores

In [18]:
df_prediction_scores_h1_clustered = pd.DataFrame(columns=['CLUSTER', 'HOSPI_CODE_UCD', 'R2', 'RMSE', 'MAE', 'MAPE'])

df_prediction_scores_h1_clustered = test_2_clustering(df_h1[features_h1], df_prediction_scores_h1_clustered, medicines)

df_prediction_scores_h1_clustered


----------------------------------------------------------------------------------------------------
Cluster: 0
Size of data set: 1157
Size of training set: 1035
Size of test set: 122
Size of grid search: 612
Finished training

----------------------------------------------------------------------------------------------------
Medicine:3400892761695
Best Parameters:  {'max_depth': 7, 'max_features': 'sqrt', 'n_estimators': 2}
Training Score (MAPE):  -9.619
----------Test scores----------
R^2 Score: -256.17
MAE: 2227.402
MAPE: 1.411
RMSE: 4270.208





----------------------------------------------------------------------------------------------------
Medicine:3400892761527
Best Parameters:  {'max_depth': 7, 'max_features': 'sqrt', 'n_estimators': 2}
Training Score (MAPE):  -9.619
----------Test scores----------
R^2 Score: -5.61
MAE: 2844.259
MAPE: 5.494
RMSE: 4048.73





----------------------------------------------------------------------------------------------------
Medicine:3400892508566
Best Parameters:  {'max_depth': 7, 'max_features': 'sqrt', 'n_estimators': 2}
Training Score (MAPE):  -9.619
----------Test scores----------
R^2 Score: -6.988
MAE: 1425.704
MAPE: 0.412
RMSE: 1539.386





----------------------------------------------------------------------------------------------------
Medicine:3400891191226
Best Parameters:  {'max_depth': 7, 'max_features': 'sqrt', 'n_estimators': 2}
Training Score (MAPE):  -9.619
----------Test scores----------
R^2 Score: -12.101
MAE: 1394.324
MAPE: 0.542
RMSE: 1791.762





----------------------------------------------------------------------------------------------------
Medicine:3400892669236
Best Parameters:  {'max_depth': 7, 'max_features': 'sqrt', 'n_estimators': 2}
Training Score (MAPE):  -9.619
----------Test scores----------
R^2 Score: 0.416
MAE: 2201.534
MAPE: 0.43
RMSE: 2480.71



...



----------------------------------------------------------------------------------------------------
Medicine:3400893826706
Best Parameters:  {'max_depth': 7, 'max_features': 'sqrt', 'n_estimators': 2}
Training Score (MAPE):  -9.619
----------Test scores----------
R^2 Score: -1.671
MAE: 1304.081
MAPE: 0.466
RMSE: 1575.261





----------------------------------------------------------------------------------------------------
Medicine:3400893875490
Best Parameters:  {'max_depth': 7, 'max_features': 'sqrt', 'n_estimators': 2}
Training Score (MAPE):  -9.619
----------Test scores----------
R^2 Score: -0.875
MAE: 3646.217
MAPE: 0.713
RMSE: 4087.939





----------------------------------------------------------------------------------------------------
Medicine:3400891996128
Best Parameters:  {'max_depth': 7, 'max_features': 'sqrt', 'n_estimators': 2}
Training Score (MAPE):  -9.619
----------Test scores----------
R^2 Score: -1.371
MAE: 1446.173
MAPE: 44.728
RMSE: 1901.747





----------------------------------------------------------------------------------------------------
Cluster: 1
Size of data set: 51
Size of training set: 45
Size of test set: 6
Size of grid search: 18
Finished training

----------------------------------------------------------------------------------------------------
Medicine:3400891996128
Best Parameters:  {'max_depth': 7, 'max_features': 'sqrt', 'n_estimators': 4}
Training Score (MAPE):  -0.131
----------Test scores----------
R^2 Score: 0.739
MAE: 3785.002
MAPE: 0.087
RMSE: 5444.906



CLUSTER          HOSPI_CODE_UCD          R2         RMSE          MAE  \
0        0  CODE_UCD_3400892761695 -256.170045  4270.208160  2227.401715   
1        0  CODE_UCD_3400892761527   -5.609822  4048.730221  2844.259301   
2        0  CODE_UCD_3400892508566   -6.987752  1539.386135  1425.704361   
3        0  CODE_UCD_3400891191226  -12.100754  1791.762448  1394.323669   
4        0  CODE_UCD_3400892669236    0.416072  2480.709585  2201.534241   
5        0  CODE_UCD_3400892203645  -10.492386  1592.069599  1376.886562   
6        0  CODE_UCD_3400892052120  -51.563108  1059.060491   867.454187   
7        0  CODE_UCD_3400892075761  -34.084019  2525.148963  1905.296696   
8        0  CODE_UCD_3400892697789 -151.555908  4185.796268  2955.684767   
9        0  CODE_UCD_3400892745848  -10.904587  5529.499951  5430.903518   
10       0  CODE_UCD_3400891225037    0.107328  4205.823486  3506.122376   
11       0  CODE_UCD_3400890837149   -3.970589  2421.585787  1629.995339   
12       0  CODE_UCD_3400893736135  -22.382752  2077.044330  1463.056717   
13       0  CODE_UCD_3400892729589   -0.814062  1833.116292  1755.820967   
14       0  CODE_UCD_3400892065366   -1.209850  1789.148769  1305.122699   
15       0  CODE_UCD_3400893022634    0.411256   987.002546   755.276148   
16       0  CODE_UCD_3400891235203  -26.154784  3572.018010  2363.302431   
17       0  CODE_UCD_3400892088310   -3.297347  1749.919971  1302.760743   
18       0  CODE_UCD_3400893826706   -1.671426  1575.261472  1304.080752   
19       0  CODE_UCD_3400893875490   -0.874811  4087.938678  3646.217114   
20       0  CODE_UCD_3400891996128   -1.371219  1901.747292  1446.173489   
21       1  CODE_UCD_3400891996128    0.738781  5444.905773  3785.002480   

         MAPE  
0    1.411360  
1    5.494029  
2    0.411704  
3    0.541811  
4    0.430017  
5    9.597550  
6    0.341012  
7   10.652153  
8    2.962651  
9    0.731254  
10   0.584878  
11   6.099986  
12   0.772850  
13   0.476127  
14   0.322170  
15   1.407768  
16   1.540737  
17  32.846746  
18   0.465835  
19   0.712738  
20  44.728460  
21   0.087500

In [25]:
df_prediction_scores_h2_clustered = pd.DataFrame(columns=['CLUSTER', 'HOSPI_CODE_UCD', 'R2', 'RMSE', 'MAE', 'MAPE'])

df_prediction_scores_h2_clustered = test_2_clustering(df_h2[features_h2], df_prediction_scores_h2_clustered, medicines)

df_prediction_scores_h2_clustered


----------------------------------------------------------------------------------------------------
Cluster: 1
There is only one sample
Size of data set: 479
Size of training set: 421
Size of test set: 58
Size of grid search: 246
Finished training

----------------------------------------------------------------------------------------------------
Medicine:3400890837149
Best Parameters:  {'max_depth': 7, 'max_features': 'sqrt', 'n_estimators': 3}
Training Score (MAPE):  -0.839
----------Test scores----------
R^2 Score: -11.828
MAE: 644.511
MAPE: 0.235
RMSE: 841.58





----------------------------------------------------------------------------------------------------
Medicine:3400893826706
Best Parameters:  {'max_depth': 7, 'max_features': 'sqrt', 'n_estimators': 3}
Training Score (MAPE):  -0.839
----------Test scores----------
R^2 Score: -5.835
MAE: 705.626
MAPE: 0.336
RMSE: 751.76





----------------------------------------------------------------------------------------------------
Medicine:3400891235203
Best Parameters:  {'max_depth': 7, 'max_features': 'sqrt', 'n_estimators': 3}
Training Score (MAPE):  -0.839
----------Test scores----------
R^2 Score: -110.517
MAE: 1582.041
MAPE: 1.425
RMSE: 1661.337





----------------------------------------------------------------------------------------------------
Medicine:3400892065366
Best Parameters:  {'max_depth': 7, 'max_features': 'sqrt', 'n_estimators': 3}
Training Score (MAPE):  -0.839
----------Test scores----------
R^2 Score: -52.215
MAE: 2373.707
MAPE: 0.439
RMSE: 2469.308





----------------------------------------------------------------------------------------------------
Medicine:3400892745848
Best Parameters:  {'max_depth': 7, 'max_features': 'sqrt', 'n_estimators': 3}
Training Score (MAPE):  -0.839
----------Test scores----------
R^2 Score: 0.567
MAE: 376.802
MAPE: 0.131
RMSE: 404.541



...



----------------------------------------------------------------------------------------------------
Medicine:3400892065366
Best Parameters:  {'max_depth': 7, 'max_features': 'sqrt', 'n_estimators': 3}
Training Score (MAPE):  -0.296
----------Test scores----------
R^2 Score: -97.147
MAE: 1615.377
MAPE: 0.184
RMSE: 1718.853





----------------------------------------------------------------------------------------------------
Medicine:3400891225037
Best Parameters:  {'max_depth': 7, 'max_features': 'sqrt', 'n_estimators': 3}
Training Score (MAPE):  -0.296
----------Test scores----------
R^2 Score: -32.277
MAE: 11450.051
MAPE: 0.557
RMSE: 13624.178





----------------------------------------------------------------------------------------------------
Medicine:3400893022634
Best Parameters:  {'max_depth': 7, 'max_features': 'sqrt', 'n_estimators': 3}
Training Score (MAPE):  -0.296
----------Test scores----------
R^2 Score: nan
MAE: 4155.736
MAPE: 0.582
RMSE: 4155.736



/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_regression.py:918: UndefinedMetricWarning:

R^2 score is not well-defined with less than two samples.



CLUSTER          HOSPI_CODE_UCD            R2          RMSE           MAE  \
0        1  CODE_UCD_3400890837149    -11.827789    841.579879    644.511117   
1        1  CODE_UCD_3400893826706     -5.834532    751.760293    705.626179   
2        1  CODE_UCD_3400891235203   -110.516770   1661.336829   1582.040717   
3        1  CODE_UCD_3400892065366    -52.214883   2469.307797   2373.706597   
4        1  CODE_UCD_3400892745848      0.566847    404.540834    376.802016   
5        1  CODE_UCD_3400893736135    -76.800458   1095.537931   1081.100453   
6        1  CODE_UCD_3400892088310      0.670443    215.649230    212.352315   
7        1  CODE_UCD_3400892729589     -0.768850   1280.849959    930.169641   
8        1  CODE_UCD_3400892203645     -2.782277    638.407403    530.169081   
9        1  CODE_UCD_3400892052120    -16.109688   1407.131349   1351.758311   
10       1  CODE_UCD_3400893022634    -19.019568   2688.651961   2599.963186   
11       1  CODE_UCD_3400892697789    -46.466882   1581.145586   1490.648132   
12       1  CODE_UCD_3400892075761     -6.672203    992.793176    845.241244   
13       1  CODE_UCD_3400892508566 -93129.534797   2877.198248   2876.938252   
14       1  CODE_UCD_3400891191226     -0.539518    870.903246    694.748683   
15       1  CODE_UCD_3400892669236           NaN   3234.506173   3234.506173   
16       0  CODE_UCD_3400893875490    -28.840746   2393.055225   2186.676336   
17       0  CODE_UCD_3400892761695    -51.284131   5567.647228   5252.702783   
18       0  CODE_UCD_3400892669236   -118.496524   3622.982004   3242.033201   
19       0  CODE_UCD_3400891996128    -36.078804  61259.249797  59369.944147   
20       0  CODE_UCD_3400892761527    -58.438807   7593.759489   4437.038894   
21       0  CODE_UCD_3400892065366    -97.147372   1718.853319   1615.377485   
22       0  CODE_UCD_3400891225037    -32.277138  13624.177565  11450.050822   
23       0  CODE_UCD_3400893022634           NaN   4155.735978   4155.735978   

         MAPE  
0    0.234965  
1    0.335678  
2    1.424721  
3    0.439297  
4    0.131003  
5    0.257141  
6    0.080579  
7    0.173627  
8    0.191042  
9    0.762614  
10   0.487040  
11   1.549255  
12   0.398227  
13  52.027009  
14   0.376594  
15   0.479044  
16   0.253366  
17   0.334631  
18   0.404190  
19   0.785006  
20   0.399678  
21   0.184371  
22   0.556603  
23   0.581629

In [26]:
df_prediction_scores_h3_clustered = pd.DataFrame(columns=['CLUSTER', 'HOSPI_CODE_UCD', 'R2', 'RMSE', 'MAE', 'MAPE'])

df_prediction_scores_h3_clustered = test_2_clustering(df_h3[features_h3], df_prediction_scores_h3_clustered, medicines)

df_prediction_scores_h3_clustered


----------------------------------------------------------------------------------------------------
Cluster: 1
Size of data set: 670
Size of training set: 587
Size of test set: 83
Size of grid search: 342
Finished training

----------------------------------------------------------------------------------------------------
Medicine:3400891996128
Best Parameters:  {'max_depth': 7, 'max_features': 'sqrt', 'n_estimators': 2}
Training Score (MAPE):  -1.024
----------Test scores----------
R^2 Score: -444.013
MAE: 96424.758
MAPE: 0.941
RMSE: 96542.614





----------------------------------------------------------------------------------------------------
Medicine:3400890837149
Best Parameters:  {'max_depth': 7, 'max_features': 'sqrt', 'n_estimators': 2}
Training Score (MAPE):  -1.024
----------Test scores----------
R^2 Score: -32.848
MAE: 2560.855
MAPE: 0.711
RMSE: 2609.445





----------------------------------------------------------------------------------------------------
Medicine:3400892761695
Best Parameters:  {'max_depth': 7, 'max_features': 'sqrt', 'n_estimators': 2}
Training Score (MAPE):  -1.024
----------Test scores----------
R^2 Score: -282.713
MAE: 18770.871
MAPE: 0.734
RMSE: 18885.465





----------------------------------------------------------------------------------------------------
Medicine:3400891235203
Best Parameters:  {'max_depth': 7, 'max_features': 'sqrt', 'n_estimators': 2}
Training Score (MAPE):  -1.024
----------Test scores----------
R^2 Score: -15.324
MAE: 1760.165
MAPE: 0.366
RMSE: 1804.694





----------------------------------------------------------------------------------------------------
Medicine:3400891225037
Best Parameters:  {'max_depth': 7, 'max_features': 'sqrt', 'n_estimators': 2}
Training Score (MAPE):  -1.024
----------Test scores----------
R^2 Score: -9.973
MAE: 3006.71
MAPE: 0.378
RMSE: 3052.914



...



----------------------------------------------------------------------------------------------------
Medicine:3400892669236
Best Parameters:  {'max_depth': 7, 'max_features': 'sqrt', 'n_estimators': 2}
Training Score (MAPE):  -1.331
----------Test scores----------
R^2 Score: -71.417
MAE: 4135.889
MAPE: 0.411
RMSE: 4947.801





----------------------------------------------------------------------------------------------------
Medicine:3400891996128
Best Parameters:  {'max_depth': 7, 'max_features': 'sqrt', 'n_estimators': 2}
Training Score (MAPE):  -1.331
----------Test scores----------
R^2 Score: -186.281
MAE: 86274.644
MAPE: 0.93
RMSE: 86422.415





----------------------------------------------------------------------------------------------------
Medicine:3400892508566
Best Parameters:  {'max_depth': 7, 'max_features': 'sqrt', 'n_estimators': 2}
Training Score (MAPE):  -1.331
----------Test scores----------
R^2 Score: -16.087
MAE: 2075.575
MAPE: 0.448
RMSE: 2562.587





----------------------------------------------------------------------------------------------------
Medicine:3400892761695
Best Parameters:  {'max_depth': 7, 'max_features': 'sqrt', 'n_estimators': 2}
Training Score (MAPE):  -1.331
----------Test scores----------
R^2 Score: -121.445
MAE: 19588.049
MAPE: 0.735
RMSE: 19726.134



CLUSTER          HOSPI_CODE_UCD           R2          RMSE           MAE  \
0        1  CODE_UCD_3400891996128  -444.012975  96542.614149  96424.758432   
1        1  CODE_UCD_3400890837149   -32.848213   2609.444891   2560.855070   
2        1  CODE_UCD_3400892761695  -282.713466  18885.465065  18770.870818   
3        1  CODE_UCD_3400891235203   -15.323884   1804.694160   1760.165171   
4        1  CODE_UCD_3400891225037    -9.973188   3052.913849   3006.710486   
5        1  CODE_UCD_3400892669236   -11.216885   5182.825567   5059.520963   
6        1  CODE_UCD_3400893826706     0.762084    561.888873    448.750000   
7        1  CODE_UCD_3400893736135    -7.729219   1028.237374    947.411829   
8        1  CODE_UCD_3400892697789   -82.055919   3886.617468   3857.375038   
9        1  CODE_UCD_3400891191226   -12.692587   1890.621541   1679.516627   
10       1  CODE_UCD_3400892052120  -274.105711   5068.163017   4992.195963   
11       1  CODE_UCD_3400892065366   -16.268168   1879.398307   1537.445035   
12       1  CODE_UCD_3400893875490   -67.175086   7053.120454   7042.114645   
13       1  CODE_UCD_3400892088310  -169.358799   1377.914660   1134.925149   
14       1  CODE_UCD_3400892745848 -1599.774878   6694.900790   6678.992291   
15       1  CODE_UCD_3400892508566  -181.122284   6035.644946   4888.121559   
16       1  CODE_UCD_3400892729589    -5.313083   1228.214623   1081.020459   
17       1  CODE_UCD_3400893022634  -498.289648   3256.753167   3206.272576   
18       1  CODE_UCD_3400892761527  -113.445919  23987.938710  23787.759774   
19       1  CODE_UCD_3400892075761 -3379.066413   4357.952290   4321.713586   
20       1  CODE_UCD_3400892203645    -3.664914   1927.718763   1801.905979   
21       0  CODE_UCD_3400893875490  -131.837439   8109.567990   7028.650107   
22       0  CODE_UCD_3400892052120  -522.171388   5725.949434   4995.032403   
23       0  CODE_UCD_3400892761527  -139.487385  23732.017534  23575.414115   
24       0  CODE_UCD_3400891191226   -55.343250   3312.688397   2426.686290   
25       0  CODE_UCD_3400891225037   -10.867850   5496.138266   5362.564949   
26       0  CODE_UCD_3400892088310  -186.817487   7695.662451   4107.754106   
27       0  CODE_UCD_3400892075761  -549.301190   4504.703805   4012.253057   
28       0  CODE_UCD_3400892203645   -18.601940   4353.644300   3546.684894   
29       0  CODE_UCD_3400892729589   -44.436963   3390.969673   2834.873967   
30       0  CODE_UCD_3400891235203  -267.197205   4942.649639   4910.553108   
31       0  CODE_UCD_3400890837149   -91.374999   4905.945975   3250.102276   
32       0  CODE_UCD_3400892065366   -17.345111   3830.981465   3324.291046   
33       0  CODE_UCD_3400892697789  -111.285675   5761.889040   4731.307657   
34       0  CODE_UCD_3400893022634  -326.895799   6105.414565   5103.519364   
35       0  CODE_UCD_3400893736135  -109.940565   6527.541960   4689.692522   
36       0  CODE_UCD_3400892745848 -3245.600506   9417.699696   7139.279749   
37       0  CODE_UCD_3400893826706   -29.571556   5319.723906   4042.048811   
38       0  CODE_UCD_3400892669236   -71.416819   4947.801177   4135.889169   
39       0  CODE_UCD_3400891996128  -186.281338  86422.415346  86274.643724   
40       0  CODE_UCD_3400892508566   -16.086999   2562.587381   2075.575129   
41       0  CODE_UCD_3400892761695  -121.445270  19726.133760  19588.049059   

         MAPE  
0    0.941121  
1    0.710740  
2    0.733705  
3    0.365912  
4    0.377952  
5    0.470749  
6    0.078274  
7    0.160143  
8    1.790278  
9    0.361291  
10   3.249382  
11   0.218440  
12   0.549128  
13   0.222188  
14  19.048153  
15   1.160683  
16   0.170440  
17   0.897014  
18   0.796879  
19   1.903148  
20   0.393253  
21   0.498458  
22   3.581279  
23   0.770474  
24   0.378112  
25   0.481463  
26   0.711866  
27   1.706358  
28   0.729575  
29   0.422957  
30   4.624081  
31   0.853277  
32   0.444426  
33   2.376362  
34   1.307534  
35   0.866471  
36  22.921323

In [27]:
df_prediction_scores_h4_clustered = pd.DataFrame(columns=['CLUSTER', 'HOSPI_CODE_UCD', 'R2', 'RMSE', 'MAE', 'MAPE'])

df_prediction_scores_h4_clustered = test_2_clustering(df_h4[features_h4], df_prediction_scores_h4_clustered, medicines)

df_prediction_scores_h4_clustered


----------------------------------------------------------------------------------------------------
Cluster: 0
Size of data set: 731
Size of training set: 654
Size of test set: 77
Size of grid search: 384
Finished training

----------------------------------------------------------------------------------------------------
Medicine:3400891191226
Best Parameters:  {'max_depth': 7, 'max_features': 'sqrt', 'n_estimators': 3}
Training Score (MAPE):  -0.45
----------Test scores----------
R^2 Score: -13.456
MAE: 3641.25
MAPE: 0.443
RMSE: 4757.039





----------------------------------------------------------------------------------------------------
Medicine:3400891235203
Best Parameters:  {'max_depth': 7, 'max_features': 'sqrt', 'n_estimators': 3}
Training Score (MAPE):  -0.45
----------Test scores----------
R^2 Score: -8.249
MAE: 4924.481
MAPE: 1.172
RMSE: 5324.816





----------------------------------------------------------------------------------------------------
Medicine:3400893736135
Best Parameters:  {'max_depth': 7, 'max_features': 'sqrt', 'n_estimators': 3}
Training Score (MAPE):  -0.45
----------Test scores----------
R^2 Score: -11.713
MAE: 4878.207
MAPE: 0.695
RMSE: 5191.196





----------------------------------------------------------------------------------------------------
Medicine:3400890837149
Best Parameters:  {'max_depth': 7, 'max_features': 'sqrt', 'n_estimators': 3}
Training Score (MAPE):  -0.45
----------Test scores----------
R^2 Score: -1.513
MAE: 5190.156
MAPE: 0.29
RMSE: 5590.133





----------------------------------------------------------------------------------------------------
Medicine:3400892508566
Best Parameters:  {'max_depth': 7, 'max_features': 'sqrt', 'n_estimators': 3}
Training Score (MAPE):  -0.45
----------Test scores----------
R^2 Score: -187.331
MAE: 4727.676
MAPE: 0.697
RMSE: 5181.368



...



----------------------------------------------------------------------------------------------------
Medicine:3400893826706
Best Parameters:  {'max_depth': 7, 'max_features': 'sqrt', 'n_estimators': 3}
Training Score (MAPE):  -0.45
----------Test scores----------
R^2 Score: -70.282
MAE: 8661.864
MAPE: 1.621
RMSE: 8837.353





----------------------------------------------------------------------------------------------------
Medicine:3400893022634
Best Parameters:  {'max_depth': 7, 'max_features': 'sqrt', 'n_estimators': 3}
Training Score (MAPE):  -0.45
----------Test scores----------
R^2 Score: -515.022
MAE: 8510.289
MAPE: 5.003
RMSE: 8518.547





----------------------------------------------------------------------------------------------------
Medicine:3400892745848
Best Parameters:  {'max_depth': 7, 'max_features': 'sqrt', 'n_estimators': 3}
Training Score (MAPE):  -0.45
----------Test scores----------
R^2 Score: -0.162
MAE: 2413.477
MAPE: 0.18
RMSE: 2712.895





----------------------------------------------------------------------------------------------------
Cluster: 1
Size of data set: 39
Size of training set: 35
Size of test set: 4
Size of grid search: 12
Finished training

----------------------------------------------------------------------------------------------------
Medicine:3400891996128
Best Parameters:  {'max_depth': 5, 'max_features': 'sqrt', 'n_estimators': 3}
Training Score (MAPE):  -0.11
----------Test scores----------
R^2 Score: 0.048
MAE: 19716.691
MAPE: 0.106
RMSE: 21591.77



CLUSTER          HOSPI_CODE_UCD          R2          RMSE           MAE  \
0        0  CODE_UCD_3400891191226  -13.455998   4757.038941   3641.249582   
1        0  CODE_UCD_3400891235203   -8.248903   5324.816152   4924.481057   
2        0  CODE_UCD_3400893736135  -11.712950   5191.195754   4878.207335   
3        0  CODE_UCD_3400890837149   -1.513035   5590.132907   5190.155891   
4        0  CODE_UCD_3400892508566 -187.330932   5181.368007   4727.675731   
5        0  CODE_UCD_3400893875490  -40.297323  11148.876941  10989.390152   
6        0  CODE_UCD_3400892052120   -4.834008   4223.111699   3021.978516   
7        0  CODE_UCD_3400892203645   -8.549324   5019.194197   4022.418735   
8        0  CODE_UCD_3400892729589   -5.287957   5545.182760   4657.702325   
9        0  CODE_UCD_3400892065366  -13.638617  10247.529398   9631.325986   
10       0  CODE_UCD_3400892088310   -5.439414   5903.107050   5146.429010   
11       0  CODE_UCD_3400891225037 -148.220508  14397.816855  14359.001145   
12       0  CODE_UCD_3400892761695  -23.648129   4389.381716   3443.100518   
13       0  CODE_UCD_3400892075761   -1.195184   1543.704234   1375.971761   
14       0  CODE_UCD_3400892761527  -25.573830   4314.891611   4193.230351   
15       0  CODE_UCD_3400892669236  -32.818317  18090.995923  17304.755684   
16       0  CODE_UCD_3400892697789   -0.633127   1932.443669   1623.763114   
17       0  CODE_UCD_3400893826706  -70.282427   8837.353050   8661.863993   
18       0  CODE_UCD_3400893022634 -515.022325   8518.546796   8510.288745   
19       0  CODE_UCD_3400892745848   -0.161791   2712.894799   2413.477119   
20       1  CODE_UCD_3400891996128    0.047517  21591.769605  19716.691300   

        MAPE  
0   0.443226  
1   1.172237  
2   0.695377  
3   0.290098  
4   0.696880  
5   0.523430  
6   0.361222  
7   0.530413  
8   0.267195  
9   0.452089  
10  1.684015  
11  0.563438  
12  0.416374  
13  0.157593  
14  0.669236  
15  0.595212  
16  0.151401  
17  1.620870  
18  5.003113  
19  0.179888  
20  0.105927